In [1]:
import sys
import os
import json

In [2]:
def load_json(data_file):
    if os.path.isfile(data_file):
        with open(data_file, 'r') as read_file:
            data = json.load(read_file)
            return data

def load_list_file(list_file):
    with open(list_file, 'r') as read_file:
        dialog_id_list = read_file.readlines()
        dialog_id_list = [l.strip('\n') for l in dialog_id_list]
        return dialog_id_list
    return

In [3]:
dialog_data_file = './MultiWOZ/data.json'
dialog_data = load_json(dialog_data_file)
dialog_id_list = list(set(dialog_data.keys())) # Bug: v1.0 contains duplicate id in the valid data
print('# of dialogs:', len(dialog_data))
# print(dialog_data['PMUL4641.json']) # print a sample dialog

# of dialogs: 10438


In [4]:
valid_list_file = './MultiWOZ/valListFile.json'
test_list_file = './MultiWOZ/testListFile.json'

valid_id_list = list(set(load_list_file(valid_list_file)))
test_id_list = load_list_file(test_list_file)
train_id_list = [did for did in dialog_id_list if did not in (valid_id_list + test_id_list)]
print('# of train dialogs:', len(train_id_list))
print('# of valid dialogs:', len(valid_id_list))
print('# of test dialogs :', len(test_id_list))
assert(len(dialog_id_list) == len(train_id_list) + len(valid_id_list) + len(test_id_list))

# of train dialogs: 8438
# of valid dialogs: 1000
# of test dialogs : 1000


In [5]:
train_data = [v for k, v in dialog_data.items() if k in train_id_list]
valid_data = [v for k, v in dialog_data.items() if k in valid_id_list]
test_data = [v for k, v in dialog_data.items() if k in test_id_list]
assert(len(train_data) == len(train_id_list))
assert(len(valid_data) == len(valid_id_list))
assert(len(test_data) == len(test_id_list))

In [6]:
train_data[0]

{'goal': {'taxi': {},
  'police': {},
  'hospital': {},
  'hotel': {'info': {'type': 'hotel',
    'parking': 'yes',
    'pricerange': 'cheap',
    'internet': 'yes'},
   'fail_info': {},
   'book': {'pre_invalid': True,
    'stay': '2',
    'day': 'tuesday',
    'invalid': False,
    'people': '6'},
   'fail_book': {'stay': '3'}},
  'topic': {'taxi': False,
   'police': False,
   'restaurant': False,
   'hospital': False,
   'hotel': False,
   'general': False,
   'attraction': False,
   'train': False,
   'booking': False},
  'attraction': {},
  'train': {},
  'message': ["You are looking for a <span class='emphasis'>place to stay</span>. The hotel should be in the <span class='emphasis'>cheap</span> price range and should be in the type of <span class='emphasis'>hotel</span>",
   "The hotel should <span class='emphasis'>include free parking</span> and should <span class='emphasis'>include free wifi</span>",
   "Once you find the <span class='emphasis'>hotel</span> you want to book it

In [7]:
def get_dst_diff(prev_d, crnt_d):
    assert len(prev_d) == len(crnt_d)
    diff = {}
    for ((k1, v1), (k2, v2)) in zip(prev_d.items(), crnt_d.items()):
        assert k1 == k2
        if v1 != v2: # updated
            diff[k2] = v2
    return diff

def analyze_dialog(d, print_dialog=True):
    assert 'log' in d
    assert 'goal' in d
    domains = []
    ignore_keys_in_goal = ['eod', 'messageLen', 'message'] # eod (probably) means the user archieved the goal. 
    for dom_k, dom_v  in d['goal'].items():
        if dom_v and dom_k not in ignore_keys_in_goal: # check whether contains some goal entities
            domains.append(dom_k)
    print('{} domain(s): {}'.format(len(domains), domains))
    
    if print_dialog:
        prev_d = None
        for i, t in enumerate(d['log']):
            spk = 'Usr' if i % 2 == 0 else 'Sys' # Turn 0 is always a user's turn in this corpus.
            if spk == 'Sys':
                if prev_d is None:
                    prev_d = t['metadata']
                else:
                    crnt_d = t['metadata']
                    dst_diff = get_dst_diff(prev_d, crnt_d)
                    print('Updated DST:', dst_diff)
                    prev_d = crnt_d
            u = t['text']
            print('{}: {}'.format(spk, u))

for d in train_data[:1]:
    print('-' * 50)
    analyze_dialog(d, True)

--------------------------------------------------
2 domain(s): ['hotel', 'topic']
Usr: am looking for a place to to stay that has cheap price range it should be in a type of hotel
Sys: Okay, do you have a specific area you want to stay in?
Usr: no, i just need to make sure it's cheap. oh, and i need parking
Updated DST: {'hotel': {'book': {'booked': [], 'stay': '', 'day': '', 'people': ''}, 'semi': {'name': 'not mentioned', 'area': 'not mentioned', 'parking': 'yes', 'pricerange': 'cheap', 'stars': 'not mentioned', 'internet': 'not mentioned', 'type': 'hotel'}}}
Sys: I found 1 cheap hotel for you that includes parking. Do you like me to book it?
Usr: Yes, please. 6 people 3 nights starting on tuesday.
Updated DST: {'hotel': {'book': {'booked': [], 'stay': '3', 'day': 'tuesday', 'people': '6'}, 'semi': {'name': 'not mentioned', 'area': 'not mentioned', 'parking': 'yes', 'pricerange': 'cheap', 'stars': 'not mentioned', 'internet': 'not mentioned', 'type': 'hotel'}}}
Sys: I am sorry but I

In [30]:
import random

answer = []
debug = False

def myprint(d):
  for k, v in d.items():
    if isinstance(v, dict):
      myprint(v)
    else:
      #print("{0} : {1}".format(k, v))            
      if k == "booked" and len(v) != 0:
            diction = v[0]
            #print(diction)
            for key, value in diction.items():
                if v is not "" and v != "not mentioned":
                    answer.append("{0}: {1}".format(key, value))
      if v is not "" and v != "not mentioned" and k != "booked" and k != "leaveAt" and k != "arriveBy" and k != "time":
          answer.append("{0}: {1}".format(k, v)) 

def convert_to_decanlp_format(d, print_dialog=True):
    global answer
    assert 'log' in d
    assert 'goal' in d
    domains = []
    ignore_keys_in_goal = ['eod', 'messageLen', 'message'] # eod (probably) means the user archieved the goal. 
    for dom_k, dom_v  in d['goal'].items():
        if dom_v and dom_k not in ignore_keys_in_goal: # check whether contains some goal entities
            domains.append(dom_k)
    print('{} domain(s): {}'.format(len(domains), domains))
    
    with open("formatted_file.jsonl", 'a+') as split_file:
        if print_dialog:
            prev_d = None
            for i, t in enumerate(d['log']):
                spk = 'Usr' if i % 2 == 0 else 'Sys' # Turn 0 is always a user's turn in this corpus.
                if spk == 'Sys':
                    if prev_d is None:
                        prev_d = t['metadata']
                    else:
                        crnt_d = t['metadata']
                        dst_diff = get_dst_diff(prev_d, crnt_d)
                        #print('Updated DST:', dst_diff)
                        
                        #Get the question
                        question = 'What is the change in state?' 
                        
                        #Get the answer
                        answer = []
                        myprint(dst_diff)
                        myString = ", ".join(answer)
                        myString += ';'
                        #print(myString)
                        
                        #Get the context
                        context = u
                        
                        prev_d = crnt_d
                        
                        ex = {'context': ' '.join(context.split()), 
                             'question': ' '.join(question.split()),
                             'answer': myString if len(myString) > 1 else 'None'
                         }
                        print(ex)
                        if ex.get("answer") == "None" and random.random() < 0.20:
                            split_file.write(json.dumps(ex) + '\n')
                        elif ex.get("answer") != "None":
                            split_file.write(json.dumps(ex) + '\n')
                            
                u = t['text']
                #print('{}: {}'.format(spk, u))

if debug:
    for d in train_data[5:10]:
        print('-' * 50)
        convert_to_decanlp_format(d, True)
else:
    for d in train_data:
        print('-' * 50)
        convert_to_decanlp_format(d, True)

--------------------------------------------------
2 domain(s): ['hotel', 'topic']
{'context': "no, i just need to make sure it's cheap. oh, and i need parking", 'question': 'What is the change in state?', 'answer': 'parking: yes, pricerange: cheap, type: hotel;'}
{'context': 'Yes, please. 6 people 3 nights starting on tuesday.', 'question': 'What is the change in state?', 'answer': 'stay: 3, day: tuesday, people: 6, parking: yes, pricerange: cheap, type: hotel;'}
{'context': 'how about only 2 nights.', 'question': 'What is the change in state?', 'answer': 'name: the cambridge belfry, reference: 7GAWK763, stay: 2, day: tuesday, people: 6, parking: yes, pricerange: cheap, type: hotel;'}
{'context': 'No, that will be all. Good bye.', 'question': 'What is the change in state?', 'answer': 'None'}
--------------------------------------------------
1 domain(s): ['police']
{'context': 'Can I please have the postcode as well?', 'question': 'What is the change in state?', 'answer': 'None'}
{'co

{'context': 'What is the postcode for this place?', 'question': 'What is the change in state?', 'answer': 'None'}
{'context': 'I need a train leaving Cambridge after 14:30', 'question': 'What is the change in state?', 'answer': 'departure: cambridge;'}
{'context': "i'm going to stevenage on wednesday.", 'question': 'What is the change in state?', 'answer': 'destination: stevenage, day: wednesday, departure: cambridge;'}
{'context': 'I need to leave after 14:30 please.', 'question': 'What is the change in state?', 'answer': 'None'}
{'context': 'What is the travel time and how much will it cose?', 'question': 'What is the change in state?', 'answer': 'None'}
{'context': 'no thanks. not necessary. thanks though. goodbye', 'question': 'What is the change in state?', 'answer': 'None'}
--------------------------------------------------
1 domain(s): ['hotel']
{'context': 'No but I need it to have free parking and cheap.', 'question': 'What is the change in state?', 'answer': 'parking: yes, pr

{'context': 'I would love to find a good british place in the centre of town.', 'question': 'What is the change in state?', 'answer': 'food: british;'}
{'context': "I'd like one in the moderate price range, please.", 'question': 'What is the change in state?', 'answer': 'food: british, pricerange: moderate;'}
{'context': 'Please make a booking for 7 people at 18:15 on Tuesday.', 'question': 'What is the change in state?', 'answer': 'name: restaurant one seven, reference: GGJCV0HF, day: tuesday, people: 7, food: british, pricerange: moderate;'}
{'context': 'I am also looking for some places to go around the restaurant. Any recommendations?', 'question': 'What is the change in state?', 'answer': 'area: centre;'}
{'context': 'What do you have near the restaurant?', 'question': 'What is the change in state?', 'answer': 'None'}
{'context': 'Alright, please tell me the phone number and address there, as well as the entrance fee', 'question': 'What is the change in state?', 'answer': 'name: a

--------------------------------------------------
3 domain(s): ['taxi', 'hotel', 'restaurant']
{'context': "It can be anywhere in town, but I'd like the hotel to be in the cheap price range if possible.", 'question': 'What is the change in state?', 'answer': 'area: dont care, parking: yes, pricerange: cheap, stars: 2;'}
{'context': 'How about in the expensive price range?', 'question': 'What is the change in state?', 'answer': 'area: dont care, parking: yes, pricerange: expensive;'}
{'context': 'I would prefer one with a rating of 2 stars.', 'question': 'What is the change in state?', 'answer': 'area: dont care, parking: yes, pricerange: expensive, stars: 2;'}
{'context': 'Yes, I would like to book it for two people for five nights, starting from Monday.', 'question': 'What is the change in state?', 'answer': 'name: express by holiday inn cambridge, reference: ZULEU3K1, people: 2, day: monday, stay: 5, area: dont care, parking: yes, pricerange: expensive, stars: 2;'}
{'context': 'I wo

--------------------------------------------------
2 domain(s): ['taxi', 'topic']
{'context': 'From Kings lynn train station.', 'question': 'What is the change in state?', 'answer': 'destination: fitzbillies restaurant, departure: kings lynn train station;'}
{'context': 'I need to leave after 20:00 please.', 'question': 'What is the change in state?', 'answer': 'phone: 07477854911, type: black volkswagen, destination: fitzbillies restaurant, departure: kings lynn train station;'}
{'context': 'Thank you goodbye', 'question': 'What is the change in state?', 'answer': 'None'}
--------------------------------------------------
3 domain(s): ['hotel', 'topic', 'train']
{'context': 'I plan to go to Cambridge and will be departing from norwich on Saturday and plan to ride a train that should arrive cambridge by 16:00.', 'question': 'What is the change in state?', 'answer': 'destination: cambridge, day: saturday, departure: norwich;'}
{'context': 'Can you give me the travel time, departure time

...

{'context': 'No, thank you. That is good. Good bye.', 'question': 'What is the change in state?', 'answer': 'None'}
--------------------------------------------------
3 domain(s): ['taxi', 'hotel', 'attraction']
{'context': 'No. that will be all. Thank you.', 'question': 'What is the change in state?', 'answer': 'None'}
{'context': "I'm also looking for a place to stay.", 'question': 'What is the change in state?', 'answer': 'None'}
{'context': "I'm looking for somewhere moderately priced with wifi.", 'question': 'What is the change in state?', 'answer': 'pricerange: moderate, internet: yes;'}
{'context': "The south. I'd like a 3 star place if you can find one.", 'question': 'What is the change in state?', 'answer': 'area: south, pricerange: moderate, stars: 3, internet: yes;'}
{'context': 'If it offers free Wifi, sure. I need a single for 3 nights starting Thursday.', 'question': 'What is the change in state?', 'answer': 'name: bridge guest house, reference: X33X44F6, stay: 3, day: th

{'context': "I don't have a preference but can you suggest one and give me their address?", 'question': 'What is the change in state?', 'answer': 'None'}
{'context': 'Thank you! Also, can you recommend a moderately-priced international restaurant, please?', 'question': 'What is the change in state?', 'answer': 'food: international, pricerange: moderate;'}
{'context': 'Thank you for the info, that will be all.', 'question': 'What is the change in state?', 'answer': 'None'}
--------------------------------------------------
4 domain(s): ['taxi', 'hotel', 'topic', 'restaurant']
{'context': 'I meant british food with that.', 'question': 'What is the change in state?', 'answer': 'food: british, area: west;'}
{'context': 'I want one in the expensive range.', 'question': 'What is the change in state?', 'answer': 'food: british, pricerange: expensive, area: west;'}
{'context': "yes for 7 at 17:15 on wednesday, I'll need the reference number then too please", 'question': 'What is the change in 

{'context': 'Please book the Marriott for 4 please.', 'question': 'What is the change in state?', 'answer': 'name: huntingdon marriott hotel, pricerange: expensive, internet: yes;'}
{'context': "I'm not sure yet. I actually just need the info. Sorry.", 'question': 'What is the change in state?', 'answer': 'None'}
{'context': 'No, that is all I need. Thank you for your help!', 'question': 'What is the change in state?', 'answer': 'None'}
--------------------------------------------------
3 domain(s): ['hotel', 'topic', 'attraction']
{'context': 'The hotel should be of the guesthouse type and should be located in the west area.', 'question': 'What is the change in state?', 'answer': 'area: west, pricerange: moderate, stars: 3, type: guesthouse;'}
{'context': 'Can you book it for me?', 'question': 'What is the change in state?', 'answer': 'name: hobsons house, area: west, pricerange: moderate, stars: 3, type: guesthouse;'}
{'context': 'book it for 7 people and 2 nights starting from satur

{'context': 'Could you find me something that includes free parking and wifi?', 'question': 'What is the change in state?', 'answer': 'parking: yes, pricerange: moderate, stars: dont care, internet: yes, type: hotel;'}
{'context': 'Great can I book a room for 7 people for 2 nights starting thursday?', 'question': 'What is the change in state?', 'answer': 'name: ashley hotel, reference: ZWCF98NW, stay: 2, day: thursday, people: 7, name: ashley hotel, parking: yes, pricerange: moderate, stars: dont care, internet: yes, type: hotel;'}
{'context': 'i am also looking for a restaurant in centre of town serving british food', 'question': 'What is the change in state?', 'answer': 'food: british, area: centre;'}
{'context': 'Not really, but can you tell me the phone number and price range for your favorite one?', 'question': 'What is the change in state?', 'answer': 'None'}
{'context': 'I need a taxi to get between the two places.', 'question': 'What is the change in state?', 'answer': 'destina

--------------------------------------------------
2 domain(s): ['attraction', 'train']
{'context': 'Somewhere in the Centre, entertainment.', 'question': 'What is the change in state?', 'answer': 'type: entertainment, area: centre;'}
{'context': 'I could also go to a college instead.', 'question': 'What is the change in state?', 'answer': 'type: college, area: centre;'}
{'context': "Can you give me the address for Christ's college please?", 'question': 'What is the change in state?', 'answer': 'None'}
{'context': 'Yes, I need a train coming from Ely on Friday.', 'question': 'What is the change in state?', 'answer': 'day: friday, departure: ely;'}
{'context': "Yes, it will need to leave after 12:30. I'll just book it for one person to cambridge.", 'question': 'What is the change in state?', 'answer': 'day: friday, departure: ely;'}
{'context': 'Yes. I need to book for one.', 'question': 'What is the change in state?', 'answer': 'trainID: TR0236, reference: 1A7ZKZ7F, people: 1, day: fri

## DB

In [8]:
hotel_db_list = load_json('./MultiWOZ/hotel_db.json')
train_db_list = load_json('./MultiWOZ/train_db.json')
attractin_db_list = load_json('./MultiWOZ/attraction_db.json')
restaurant_db_list = load_json('./MultiWOZ/restaurant_db.json')
print(hotel_db_list[0]) # print a sample entity

{'address': '124 tenison road', 'area': 'east', 'internet': 'yes', 'parking': 'no', 'id': '0', 'location': [52.1963733, 0.1987426], 'name': 'a and b guest house', 'phone': '01223315702', 'postcode': 'cb12dp', 'price': {'double': '70', 'family': '90', 'single': '50'}, 'pricerange': 'moderate', 'stars': '4', 'takesbookings': 'yes', 'type': 'guesthouse'}
